In [5]:
import pandas as pd
import numpy as np
import os, sys, json, argparse, pickle
import sumolib, traci
from tqdm import tqdm
from datetime import datetime, timedelta
path_root = os.path.dirname(os.path.dirname(os.path.abspath('.')))
path_scr = os.path.join(path_root, 'scripts')
sys.path.append(path_scr)
# from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [6]:
self = SignalGenerator()

In [7]:
self.prepare_data()
self.process_history()
self.process_movement()
self.make_histids()
self.set_timepoints()
self.assign_red_yellow()

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-5. 필요한 보조 객체들이 모두 준비되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.
4. 통합 테이블을 생성합니다.


In [8]:
self.SIGTABLE = self.SIGTABLE.reset_index(drop=True)
self.SIGTABLE

node_id  start_unix  phase  duration               state
0    106231  1722383968  1g_1g        11            grgrrGGG
1    106231  1722383968  1y_1y         4            grgrrGGy
2    106231  1722383968  2g_2g        24            grgGGGGr
3    106231  1722383968  2y_2y         4            grgyyyyr
4    106231  1722383968  3g_3g         8            gGgrrrrr
..      ...         ...    ...       ...                 ...
250  109986  1722384700  1g_1g        67  gGGGGrgrrgGGGGrgrr
251  109986  1722384700  1y_1y         4  gyyyyrgrrgyyyyrgrr
252  109986  1722384700  2g_2g        24  grrrrGgrrgrrrrGgrr
253  109986  1722384700  2y_2y         4  grrrrygrrgrrrrygrr
254  109986  1722384700  3g_3g        54  grrrrrgGGgrrrrrgrr

[255 rows x 5 columns]

In [9]:
A = range(10)
B = dict()
for a, b in zip(A[:-1], A[1:]):
    B[a, b] = a + b
B

{(0, 1): 1,
 (1, 2): 3,
 (2, 3): 5,
 (3, 4): 7,
 (4, 5): 9,
 (5, 6): 11,
 (6, 7): 13,
 (7, 8): 15,
 (8, 9): 17}

In [25]:
improper_pairs = dict()
improper_pairs['ry'] = []
improper_pairs['Gr'] = []
improper_pairs['yG'] = []
for node_id, group in self.SIGTABLE.groupby('node_id'):
    state_length = len(group.iloc[0].state)
    # 상태를 리스트로 변환
    state_lists = group['state'].apply(list)
    # 새로운 열들을 한 번에 추가
    cnxnwises = {str(j): [state[j] for state in state_lists] for j in range(state_length)}
    for state_order in cnxnwises:
        cnxnwise = cnxnwises[state_order]
        for phase_order, (p, q) in enumerate(zip(cnxnwise[:-1], cnxnwise[1:])):
            if (p, q) == ('r', 'y'):
                improper_pairs['ry'].append({'node_id':node_id, 'state_order':state_order, 'phase_order':phase_order})
            if (p, q) == ('G', 'r'):
                improper_pairs['Gr'].append({'node_id':node_id, 'state_order':state_order, 'phase_order':phase_order})
            if (p, q) == ('y', 'G'):
                improper_pairs['ry'].append({'node_id':node_id, 'state_order':state_order, 'phase_order':phase_order})
if any(value for value in improper_pairs.values()):
    print('부적절하게 연속된 신호조합(r->y, G->r, y->G)이 존재합니다 :')
    print(improper_pairs)